In [1]:
import sys
print(sys.version)

3.6.9 |Anaconda, Inc.| (default, Jul 30 2019, 13:42:17) 
[GCC 4.2.1 Compatible Clang 4.0.1 (tags/RELEASE_401/final)]


In [2]:
pip install tensorflow==2.0.1 numpy requests tqdm

Note: you may need to restart the kernel to use updated packages.


In [3]:
import tensorflow as tf
import numpy as np
import os
import pickle
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Dropout
from string import punctuation

jupyter notebook --NotebookApp.iopub_data_rate_limit=1000000000

In [4]:
#import requests
#content = requests.get("http://www.gutenberg.org/cache/epub/11/pg11.txt").text
#open("data/alltexts.txt", "w", encoding="utf-8")

In [5]:
text = ""

In [6]:
#myfile = open("D:\myfile.txt")
#myfile = open("data/alltexts.txt", "r", encoding="utf-8")
# print(len(myfile.read()))
with open("data/alltexts.txt", "r", encoding="utf-8") as myfile:
   # print(myfile.read())
    text = myfile.read()

In [7]:
print(text)

In the beginning God created the heaven and the earth.

1:2 And the earth was without form, and void; and darkness was upon
the face of the deep. And the Spirit of God moved upon the face of the
waters.

1:3 And God said, Let there be light: and there was light.

1:4 And God saw the light, that it was good: and God divided the light
from the darkness.

1:5 And God called the light Day, and the darkness he called Night.
And the evening and the morning were the first day.

1:6 And God said, Let there be a firmament in the midst of the waters,
and let it divide the waters from the waters.

1:7 And God made the firmament, and divided the waters which were
under the firmament from the waters which were above the firmament:
and it was so.

1:8 And God called the firmament Heaven. And the evening and the
morning were the second day.

1:9 And God said, Let the waters under the heaven be gathered together
unto one place, and let the dry land appear: and it was so.

1:10 And God called the dry l

In [8]:
sequence_length = 100
BATCH_SIZE = 128
EPOCHS = 3

# dataset file path

FILE_PATH = "data/alltexts.txt"
BASENAME = os.path.basename(FILE_PATH)

# read data

# remove caps, comment this code if we would like uppercase characters as well
#remove the numbers
text2 = text.lower()
# remove numbers 

# remove punctuation 

text = text2.translate(str.maketrans("", "", punctuation))


In [11]:
text = text.replace("’","").replace('“', "").replace('”', "")
text = text.replace("â","a").replace("ë", "e").replace("ï", "i")

In [12]:
# print some stats
n_chars = len(text)
vocab = ''.join(sorted(set(text)))
print("unique_chars:", vocab)
n_unique_chars = len(vocab)
print("Number of characters:", n_chars)
print("Number of unique characters:", n_unique_chars)

unique_chars: 
 0123456789abcdefghijklmnopqrstuvwxyz
Number of characters: 5248124
Number of unique characters: 39


In [13]:
# dictionary that converts characters to integers
char2int = {c: i for i, c in enumerate(vocab)}
# dictionary that converts integers to characters
int2char = {i: c for i, c in enumerate(vocab)}

In [14]:
print(char2int)
print(len(char2int))

{'\n': 0, '\x0c': 1, ' ': 2, '0': 3, '1': 4, '2': 5, '3': 6, '4': 7, '5': 8, '6': 9, '7': 10, '8': 11, '9': 12, 'a': 13, 'b': 14, 'c': 15, 'd': 16, 'e': 17, 'f': 18, 'g': 19, 'h': 20, 'i': 21, 'j': 22, 'k': 23, 'l': 24, 'm': 25, 'n': 26, 'o': 27, 'p': 28, 'q': 29, 'r': 30, 's': 31, 't': 32, 'u': 33, 'v': 34, 'w': 35, 'x': 36, 'y': 37, 'z': 38}
39


In [15]:
print(int2char)
print(len(int2char))

{0: '\n', 1: '\x0c', 2: ' ', 3: '0', 4: '1', 5: '2', 6: '3', 7: '4', 8: '5', 9: '6', 10: '7', 11: '8', 12: '9', 13: 'a', 14: 'b', 15: 'c', 16: 'd', 17: 'e', 18: 'f', 19: 'g', 20: 'h', 21: 'i', 22: 'j', 23: 'k', 24: 'l', 25: 'm', 26: 'n', 27: 'o', 28: 'p', 29: 'q', 30: 'r', 31: 's', 32: 't', 33: 'u', 34: 'v', 35: 'w', 36: 'x', 37: 'y', 38: 'z'}
39


In [16]:
#text = text.replace("\\x0c", " ")

In [20]:
# save dictionaries for later generation

pickle.dump(char2int, open(f"{BASENAME}-char2int.pickle", "wb"))
pickle.dump(int2char, open(f"{BASENAME}-int2char.pickle", "wb"))


In [21]:
# convert all text to integers
encoded_text = np.array([char2int[c] for c in text])

In [22]:
encoded_text

array([21, 26,  2, ...,  0,  0,  0])

In [23]:
# construct tf.data.Dataset object
char_dataset = tf.data.Dataset.from_tensor_slices(encoded_text)

In [24]:
# print first 5 characters

for char in char_dataset.take(8):
    print(char.numpy(), int2char[char.numpy()])
    
    #this prints characters with their respective integer representations

21 i
26 n
2  
32 t
20 h
17 e
2  
14 b


In [25]:
# build sequences by batching

sequences = char_dataset.batch(2*sequence_length + 1, drop_remainder=True)

#print sequences

for sequence in sequences.take(2):
    print(''.join([int2char[i] for i in sequence.numpy()]))
    

in the beginning god created the heaven and the earth

12 and the earth was without form and void and darkness was upon
the face of the deep and the spirit of god moved upon the face of the
waters

13 
and god said let there be light and there was light

14 and god saw the light that it was good and god divided the light
from the darkness

15 and god called the light day and the darkness he called ni


In [26]:
# Now you know how each sample is represented, let's 
# prepare our inputs and targets, we need a way to convert 
# a single sample (sequence of characters) into multiple (input, target) 
# samples. Fortunately, flat_map() method is exactly what we need, it takes 
# a callback function which loops over all our data samples:

In [27]:
def split_sample(sample):
    ds = tf.data.Dataset.from_tensors((sample[:sequence_length], sample[sequence_length]))
    for i in range(1, (len(sample)-1) // 2):
        input_ = sample[i: i+sequence_length]
        target = sample[i+sequence_length]
        
        # extend the dataset with these samples by concatenate() method
        other_ds = tf.data.Dataset.from_tensors((input_, target))
        ds = ds.concatenate(other_ds)
    return ds

# prepare inputs and targets
dataset = sequences.flat_map(split_sample)
        
        

one hot encoding

In [28]:
def one_hot_samples(input_, target):
    # onehot encode the inputs and the targets
    return tf.one_hot(input_, n_unique_chars), tf.one_hot(target, n_unique_chars)

dataset = dataset.map(one_hot_samples)

In [29]:
# print first 2 samples

for element in dataset.take(2):
    print("Input:", ''.join([int2char[np.argmax(char_vector)] for char_vector in element[0].numpy()]))
    print("Target:", int2char[np.argmax(element[1].numpy())])
    print("Input shape:", element[0].shape)
    print("Target shape:", element[0].shape)
    print("="*50, "\n")

Input: in the beginning god created the heaven and the earth

12 and the earth was without form and void an
Target: d
Input shape: (100, 39)
Target shape: (100, 39)

Input: n the beginning god created the heaven and the earth

12 and the earth was without form and void and
Target:  
Input shape: (100, 39)
Target shape: (100, 39)



In [30]:
# repeat, shuffle and batch dataset

ds = dataset.repeat().shuffle(1024).batch(BATCH_SIZE, drop_remainder=True)

# Building the Model

In [31]:
# # 2 lstm layers and 128 lstm units (arbitrary number) using Adam but we can experiment with different optimizers
# model = Sequential([
#     LSTM(256, input_shape=(sequence_length, n_unique_chars), return_sequences=True),
#     Dropout(0.3),
#     LSTM(256),
#     Dense(n_unique_chars, activation="softmax"),
# ])

# model.load_weights(f"results/{BASENAME}-{sequence_length}.h5")

# model.summary()
# model.compile(loss="categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

# if not os.path.isdir("results"):
#     os.mkdir("results")

# # checkpoint = ModelCheckpoint("results/{}-{loss:.2f}.h5".format(BASENAME), verbose=1)

# # train the model
# model.fit(ds, steps_per_epoch=(len(encoded_text) - sequence_length) // BATCH_SIZE, epochs=EPOCHS)
# # save the model
# print(f"results/{BASENAME}-{sequence_length}.h5")
# model.save(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")

# #deepkoro/data/results


OSError: Unable to open file (unable to open file: name = 'results/alltexts.txt-100.h5', errno = 2, error message = 'No such file or directory', flags = 0, o_flags = 0)

In [32]:
# 2 lstm layers and 128 lstm units (arbitrary number) using Adam but we can experiment with different optimizers
model = Sequential([
    LSTM(256, input_shape=(sequence_length, n_unique_chars), return_sequences=True),
    Dropout(0.3),
    LSTM(256),
    Dense(n_unique_chars, activation="softmax"),
])

#model.load_weights(f"results/{BASENAME}-{sequence_length}.h5")

model.summary()
model.compile(loss="categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

if not os.path.isdir("results"):
    os.mkdir("results")

# checkpoint = ModelCheckpoint("results/{}-{loss:.2f}.h5".format(BASENAME), verbose=1)

# train the model
model.fit(ds, steps_per_epoch=(len(encoded_text) - sequence_length) // BATCH_SIZE, epochs=EPOCHS)
# save the model
print(f"results/{BASENAME}-{sequence_length}.h5")
model.save(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")

#deepkoro/data/results


Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_2 (LSTM)                (None, 100, 256)          303104    
_________________________________________________________________
dropout_1 (Dropout)          (None, 100, 256)          0         
_________________________________________________________________
lstm_3 (LSTM)                (None, 256)               525312    
_________________________________________________________________
dense_1 (Dense)              (None, 39)                10023     
Total params: 838,439
Trainable params: 838,439
Non-trainable params: 0
_________________________________________________________________
Train for 41000 steps
Epoch 1/3
41000/41000 [==============================] - 41557s 1s/step - loss: 1.2249 - accuracy: 0.6283
Epoch 2/3
41000/41000 [==============================] - 40003s 976ms/step - loss: 1.0576 - accuracy: 0.6724
Epoch 3/3

In [59]:
model.load_weights(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")


In [ ]:
# import pickle
# # Save the model to your hard disk
# pickle.dump(model, open(filename, 'wb'))
# # some time later...
# # load the model from hard disk
# loaded_model = pickle.load(open(filename, 'rb'))
# result = loaded_model.score(X_test, Y_test)
# print(result)

In [ ]:
# (len(encoded_text) - sequence_length) // BATCH_SIZE

#epoch=EPOCHS)

#reference

In [ ]:
# building the model
# # model = Sequential([
# #     LSTM(128, input_shape=(sequence_length, n_unique_chars)),
# #     Dense(n_unique_chars, activation="softmax"),
# # ])

# # a better model (slower to train obviously)
# model = Sequential([
#     LSTM(256, input_shape=(sequence_length, n_unique_chars), return_sequences=True),
#     Dropout(0.3),
#     LSTM(256),
#     Dense(n_unique_chars, activation="softmax"),
# ])

# model.load_weights(f"results/{BASENAME}-{sequence_length}.h5")

# model.summary()
# model.compile(loss="categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

# if not os.path.isdir("results"):
#     os.mkdir("results")

# # checkpoint = ModelCheckpoint("results/{}-{loss:.2f}.h5".format(BASENAME), verbose=1)

# # train the model
# model.fit(ds, steps_per_epoch=(len(encoded_text) - sequence_length) // BATCH_SIZE, epochs=EPOCHS)
# # save the model
# model.save(f"results/{BASENAME}-{sequence_length}.h5")

# Generating Text


In [38]:
import tensorflow as tf
#import numpy as np
#import pickle
import tqdm
#from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Dropout, Activation
#import os

sequence_length = 100
# dataset file path
FILE_PATH = "data/alltexts.txt"
# FILE_PATH = "data/python_code.py"
BASENAME = os.path.basename(FILE_PATH)

In [39]:
char2int = pickle.load(open(f"{BASENAME}-char2int.pickle", "rb"))
int2char = pickle.load(open(f"{BASENAME}-int2char.pickle", "rb"))

sequence_length = 100
vocab_size = len(char2int)

In [40]:
#building the model

In [41]:
model = Sequential([
    LSTM(256, input_shape=(sequence_length, vocab_size), return_sequences=True),
    Dropout(0.3),
    LSTM(256),
    Dense(vocab_size, activation="softmax"),
])


In [ ]:
#load the weights

In [46]:
# load the optimal weights
model.load_weights(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")
# specify the feed to first characters to generate
seed = "in the beginning"
s = seed
n_chars = 400
# generate 400 characters

In [47]:
#"generated" function uses tqdm sequence length and vocab variable and extends
# on a given seed text prompt. There is a prediction given our trained model and then
# 

# in the beginning...

In [48]:
generated = ""
for i in tqdm.tqdm(range(n_chars), "Generating text"):
    # make the input sequence
    X = np.zeros((1, sequence_length, vocab_size))
    for t, char in enumerate(seed):
        X[0, (sequence_length - len(seed)) + t, char2int[char]] = 1
    # predict the next character
    predicted = model.predict(X, verbose=0)[0]
    # converting the vector to an integer
    next_index = np.argmax(predicted)
    # converting the integer to a character
    next_char = int2char[next_index]
    # add the character to results
    generated += next_char
    # shift seed and the predicted character
    seed = seed[1:] + next_char

print("Seed:", s)
print("Generated text:")
print(generated)

Generating text: 100%|██████████| 400/400 [00:07<00:00, 51.39it/s]

Seed: in the beginning
Generated text:

of the chief prince
and they were the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of heth and
they shall be the
sons of het


# all that we are is...

In [49]:
model.load_weights(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")
# specify the feed to first characters to generate
seed = "all that we are is"
s = seed
n_chars = 108
# generate 108 characters
generated = ""
for i in tqdm.tqdm(range(n_chars), "Generating text"):
    # make the input sequence
    X = np.zeros((1, sequence_length, vocab_size))
    for t, char in enumerate(seed):
        X[0, (sequence_length - len(seed)) + t, char2int[char]] = 1
    # predict the next character
    predicted = model.predict(X, verbose=0)[0]
    # converting the vector to an integer
    next_index = np.argmax(predicted)
    # converting the integer to a character
    next_char = int2char[next_index]
    # add the character to results
    generated += next_char
    # shift seed and the predicted character
    seed = seed[1:] + next_char

print("Seed:", s)
print("Generated text:")
print(generated)

Generating text: 100%|██████████| 108/108 [00:02<00:00, 53.25it/s]

Seed: all that we are is
Generated text:

the son of adah the
son of abraham and
the chief captain of
the chief priest and
the chief captain of
the c


# the real nature of the self....

In [51]:
model.load_weights(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")
# specify the feed to first characters to generate
seed = "the real nature of the self"
s = seed
n_chars = 180
# generate 180 characters
generated = ""
for i in tqdm.tqdm(range(n_chars), "Generating text"):
    # make the input sequence
    X = np.zeros((1, sequence_length, vocab_size))
    for t, char in enumerate(seed):
        X[0, (sequence_length - len(seed)) + t, char2int[char]] = 1
    # predict the next character
    predicted = model.predict(X, verbose=0)[0]
    # converting the vector to an integer
    next_index = np.argmax(predicted)
    # converting the integer to a character
    next_char = int2char[next_index]
    # add the character to results
    generated += next_char
    # shift seed and the predicted character
    seed = seed[1:] + next_char

print("Seed:", s)
print("Generated text:")
print(generated)

Generating text: 100%|██████████| 180/180 [00:03<00:00, 52.52it/s]

Seed: the real nature of the self
Generated text:


3112 and the chief captain of
the chief captivity of the lord
and they were the sons of her
she said unto him he had sent
them and she said unto him he
was in the sight of the lo


In [ ]:
# observe literal repeat

In [52]:
model.load_weights(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")
# specify the feed to first characters to generate
seed = "the real nature of the self"
s = seed
n_chars = 180
# generate 180 characters
generated = ""
for i in tqdm.tqdm(range(n_chars), "Generating text"):
    # make the input sequence
    X = np.zeros((1, sequence_length, vocab_size))
    for t, char in enumerate(seed):
        X[0, (sequence_length - len(seed)) + t, char2int[char]] = 1
    # predict the next character
    predicted = model.predict(X, verbose=0)[0]
    # converting the vector to an integer
    next_index = np.argmax(predicted)
    # converting the integer to a character
    next_char = int2char[next_index]
    # add the character to results
    generated += next_char
    # shift seed and the predicted character
    seed = seed[1:] + next_char

print("Seed:", s)
print("Generated text:")
print(generated)

Generating text: 100%|██████████| 180/180 [00:03<00:00, 52.32it/s]

Seed: the real nature of the self
Generated text:


3112 and the chief captain of
the chief captivity of the lord
and they were the sons of her
she said unto him he had sent
them and she said unto him he
was in the sight of the lo


# when our mind is cleansed from the dross of matter...


In [53]:
model.load_weights(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")
# specify the feed to first characters to generate
seed = "when our mind is cleansed from the dross of matter"
s = seed
n_chars = 180
# generate 180 characters
generated = ""
for i in tqdm.tqdm(range(n_chars), "Generating text"):
    # make the input sequence
    X = np.zeros((1, sequence_length, vocab_size))
    for t, char in enumerate(seed):
        X[0, (sequence_length - len(seed)) + t, char2int[char]] = 1
    # predict the next character
    predicted = model.predict(X, verbose=0)[0]
    # converting the vector to an integer
    next_index = np.argmax(predicted)
    # converting the integer to a character
    next_char = int2char[next_index]
    # add the character to results
    generated += next_char
    # shift seed and the predicted character
    seed = seed[1:] + next_char

print("Seed:", s)
print("Generated text:")
print(generated)

Generating text: 100%|██████████| 180/180 [00:03<00:00, 51.94it/s]

Seed: when our mind is cleansed from the dross of matter
Generated text:

and they were the sons of heth and they were the sons
of his brethren and they were the sons of heth and
they shall be the sons of eliphaz the son of ahim and
they said unto him h


In [54]:
model.load_weights(f"/Users/Daniel/Desktop/deepkoro/data/results{BASENAME}-{sequence_length}.h5")
# specify the feed to first characters to generate
seed = "today we are coding"
s = seed
n_chars = 100
# generate 180 characters
generated = ""
for i in tqdm.tqdm(range(n_chars), "Generating text"):
    # make the input sequence
    X = np.zeros((1, sequence_length, vocab_size))
    for t, char in enumerate(seed):
        X[0, (sequence_length - len(seed)) + t, char2int[char]] = 1
    # predict the next character
    predicted = model.predict(X, verbose=0)[0]
    # converting the vector to an integer
    next_index = np.argmax(predicted)
    # converting the integer to a character
    next_char = int2char[next_index]
    # add the character to results
    generated += next_char
    # shift seed and the predicted character
    seed = seed[1:] + next_char

print("Seed:", s)
print("Generated text:")
print(generated)

Generating text: 100%|██████████| 100/100 [00:02<00:00, 38.06it/s]

Seed: today we are coding
Generated text:

there and the chief
country of the chief
prince of the chief
prince of the chief
prince of the chie


In [56]:
print(tqdm.tqdm(range(n_chars), "Generating text"))

Generating text:   0%|          | 0/100 [00:00<?, ?it/s]

Generating text:   0%|          | 0/100 [00:00<?, ?it/s]


In [57]:
print(range(n_chars))

range(0, 100)
